#### Author: Thejasvi Beleyur
#### Last updated: 27-02-2020

This notebook will detail all the steps required to get matching audio snippets for the annotations of bat flights made for 2018-08-16 between 23:00-24:00 hours. 

This notebook is basically a copy of the one used to get annotation audio for 2018-08-17 1-2am. 

### Steps carried out before hand:
1. Generating the video sync for the video file *videosync_OrlovaChukaDome_01_20180816_23.00.00-00.00.00[R]...* with frame-wise light intensities and time stamps

2. Video annotations of the horseshoebats flying done by  Aditya Kanjoor. 


In [1]:
import matplotlib.pyplot as plt
import pandas as pd 
from tqdm import tqdm

package_folder = 'C:\\Users\\tbeleyur\\Documents\\match_audio_to_video\\bin\\'
import os
import sys 
sys.path.append(package_folder) # include the modules in the outer folder in the search path
from process_video_annotations import video_sync_over_annotation_block



In [2]:
# loading the annotations
annotations = pd.read_csv('annotations/corrected_HBC_video_annotations_Aditya/2018-08-16_2324_Aditya_corrected.csv')

In [3]:
annotations.head()

video_path  \
0  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   
1  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   
2  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   
3  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   
4  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   

              annotation_id  Sampling minute  timestamp from camera  \
0  Aditya_2018-08-16_2324_1                0                      2   
1  Aditya_2018-08-16_2324_2                0                      2   
2  Aditya_2018-08-16_2324_3                0                      2   
3  Aditya_2018-08-16_2324_4                1                      2   
4  Aditya_2018-08-16_2324_5                2                      2   

       start_timestamp  start_framenumber        end_timestamp  \
0  2018-08-16 23:00:50                 15  2018-08-16 23:00:56   
1  2018-08-16 23:00:56                 11  2018-08-16 23:00:56   
2  2018-08-16 23:00:57                  5  2018-08-16 23:00:58   
3  2018-08-16 23:01:10                 14  2018-08-16 23:01:11   
4  2018-08-16 23:02:17                 14  2018-08-16 23:02:18   

   end_framenumber  no. of flying bats bat behaviour  \
0                4                   1           NaN   
1               23                   2           NaN   
2               18                   1           NaN   
3                9                   1           NaN   
4                4                   1           NaN   

   strength (1 - strong, 0-weak) weak in (Behaviour Be, Number Bn) Comments  \
0                              1                               NaN      NaN   
1                              1                               NaN      NaN   
2                              1                               NaN      NaN   
3                              1                               NaN      NaN   
4                              1                               NaN      NaN   

   Details on the comment annotator  
0                     NaN    Aditya  
1                     NaN    Aditya  
2                     NaN    Aditya  
3                     NaN    Aditya  
4                     NaN    Aditya

In [4]:
annotations.shape

(289, 15)

In [5]:
annots_w_bats = annotations[annotations['no. of flying bats']>0].reset_index(drop=True)

In [6]:
annotations.shape

(289, 15)

In [7]:
annots_w_bats.shape

(289, 15)

In [8]:
annots_w_bats.head()

video_path  \
0  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   
1  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   
2  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   
3  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   
4  OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...   

              annotation_id  Sampling minute  timestamp from camera  \
0  Aditya_2018-08-16_2324_1                0                      2   
1  Aditya_2018-08-16_2324_2                0                      2   
2  Aditya_2018-08-16_2324_3                0                      2   
3  Aditya_2018-08-16_2324_4                1                      2   
4  Aditya_2018-08-16_2324_5                2                      2   

       start_timestamp  start_framenumber        end_timestamp  \
0  2018-08-16 23:00:50                 15  2018-08-16 23:00:56   
1  2018-08-16 23:00:56                 11  2018-08-16 23:00:56   
2  2018-08-16 23:00:57                  5  2018-08-16 23:00:58   
3  2018-08-16 23:01:10                 14  2018-08-16 23:01:11   
4  2018-08-16 23:02:17                 14  2018-08-16 23:02:18   

   end_framenumber  no. of flying bats bat behaviour  \
0                4                   1           NaN   
1               23                   2           NaN   
2               18                   1           NaN   
3                9                   1           NaN   
4                4                   1           NaN   

   strength (1 - strong, 0-weak) weak in (Behaviour Be, Number Bn) Comments  \
0                              1                               NaN      NaN   
1                              1                               NaN      NaN   
2                              1                               NaN      NaN   
3                              1                               NaN      NaN   
4                              1                               NaN      NaN   

   Details on the comment annotator  
0                     NaN    Aditya  
1                     NaN    Aditya  
2                     NaN    Aditya  
3                     NaN    Aditya  
4                     NaN    Aditya

### Carrying out the common-fps conversion:


In [9]:
# load the video sync file with corrected timestamps
video_sync_file = 'videosync_OrlovaChukaDome_01_20180816_23.00.00-00.00.00[R][@f6b][1].avi_[timestamp_corrected]_[signal_checked].csv'
path_to_videosync = os.path.join('raw_sync',
                                 video_sync_file)
video_sync = pd.read_csv(path_to_videosync)

kwargs = {'timestamp_pattern': '%Y-%m-%d %H:%M:%S'}
kwargs['min_fps']= 21 # Hz
kwargs['min_durn'] = 45.0 # seconds 
kwargs['common_fps'] = 25 # Hz
kwargs['output_folder'] = './common_fps/Aditya_annotations/2018-08-16/'

In [10]:
annots_w_bats['start_framenumber'].dtype

dtype('int64')

In [11]:
unprocessed_annotations = []

for i, each_annotation in tqdm(annots_w_bats.iterrows()):
    try:
        success = video_sync_over_annotation_block(each_annotation,video_sync, 
                                                     **kwargs)
    except :
        unprocessed_annotations.append(i)
        print('Unable to process annotation: %s'%annots_w_bats['annotation_id'][i])


0it [00:00, ?it/s]C:\Users\tbeleyur\AppData\Local\Continuum\anaconda2\envs\horseshoebat\lib\site-packages\scipy\signal\signaltools.py:2223: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  Y[sl] = X[sl]
C:\Users\tbeleyur\AppData\Local\Continuum\anaconda2\envs\horseshoebat\lib\site-packages\scipy\signal\signaltools.py:2225: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  Y[sl] = X[sl]
C:\Users\tbeleyur\AppData\Local\Continuum\anaconda2\envs\horseshoebat\lib\site-packages\scipy\signal\signaltools.py:2233: FutureWarning: Using a non-tuple sequenc

Saved annotation :Aditya_2018-08-16_2324_1


1it [00:05,  5.24s/it]

Unable to process annotation: Aditya_2018-08-16_2324_2


2it [00:10,  5.22s/it]

...

287it [23:53,  4.59s/it]

('2018-08-17 00:00:01', '...to...', '2018-08-17 00:00:13')
video_path                           OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...
annotation_id                                               Aditya_2018-08-16_2324_289
Sampling minute                                                                     59
timestamp from camera                                                                2
start_timestamp                                                    2018-08-16 23:59:28
start_framenumber                                                                   13
end_timestamp                                                      2018-08-16 23:59:29
end_framenumber                                                                      3
no. of flying bats                                                                   1
bat behaviour                                                                      NaN
strength (1 - strong, 0-weak)                                          

288it [23:55,  3.74s/it]

('2018-08-17 00:00:32', '...to...', '2018-08-17 00:00:31')
video_path                           OrlovaChukaDome_02_20180816_23.00.00-00.00.00[...
annotation_id                                               Aditya_2018-08-16_2324_290
Sampling minute                                                                     59
timestamp from camera                                                                2
start_timestamp                                                    2018-08-16 23:59:55
start_framenumber                                                                    1
end_timestamp                                                      2018-08-16 23:59:57
end_framenumber                                                                      9
no. of flying bats                                                                   1
bat behaviour                                                                      NaN
strength (1 - strong, 0-weak)                                          

289it [23:56,  3.14s/it]


In [12]:
len(unprocessed_annotations)

51

### Matching Audio from the common_fps files

In [19]:
### Finding the matching audio snippet !! 
import glob 
import soundfile as sf
from audio_for_videoannotation import match_video_sync_to_audio, search_for_best_fit

#all_commonfps = glob.glob('common_fps_video_sync*') # get all the relevant common_fps_sync files
all_commonfps = glob.glob('common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324*')
audio_folder = 'C://Users//tbeleyur//Documents//horseshoe_bat//2018-08-16//non_spikey//' # the current folder

# the output folders
audiosync_folder = './sync_audio/'
audioannotation_folder = './annotation_audio/'
fs = 250000 # change according to the recording sampling rate in Hz!! 


In [20]:
all_ccs = []
files_to_run = sorted(all_commonfps)

def generate_matching_audio(each_commonfps, audio_folder, 
                           **kwargs):
    '''
    '''
    print(each_commonfps)
    try:
        video_sync = pd.read_csv(each_commonfps)
        best_audio, syncblock_audio, crosscoef = match_video_sync_to_audio(video_sync, audio_folder, 
                                                                           **kwargs)
        all_ccs.append(crosscoef)
        fname  = os.path.split(each_commonfps)[-1]
        annotation_id = '-'.join(os.path.split(fname)[-1].split('common_fps_video_sync')[-1:])[:-4]

        audiosync_folder = kwargs.get('audiosync_folder', 'sync_audio')
        audioannotation_folder = kwargs.get('audioannotation_folder', 'annotation_audio')

    
        audio_file_base_name = annotation_id+'.WAV'
        sf.write(audiosync_folder+'matching_sync_'+audio_file_base_name, syncblock_audio,fs)
        sf.write(audioannotation_folder+'matching_annotaudio_'+audio_file_base_name, best_audio,fs)
        return(True)
    except:
        print('Could not save ', each_commonfps)
        return(False)



In [21]:
all_commonfps

['common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_1.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_10.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_100.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_101.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_102.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_103.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_104.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_107.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_108.csv',
 'common_fps\\Aditya_annotations\\2018-08-16\\common_fps_video_syncAditya_2018-08-16_2324_109.csv',
 'c

In [17]:
audio_folder

'C://Users//tbeleyur//Documents//horseshoe_bat//2018-08-16//non_spikey//'

In [22]:
len(all_commonfps)

196

In [23]:
for each in all_commonfps:
    generate_matching_audio(each, audio_folder, audio_sync_spikey=False, file_subset=('non_spikey_T0000315',
                                                                                      'non_spikey_T0000385'),
                            audio_fileformat='*.WAV',
                          audiosync_folder='sync_audio/Aditya_annotations/',
                           audioannotation_folder='annotation_audio/Aditya_annotations/')


common_fps\Aditya_annotations\2018-08-16\common_fps_video_syncAditya_2018-08-16_2324_1.csv
('video_fps obtained is :', 25)
Did not find user-provided sample rate - getting it from first file that matches format!
('sampling rate is : ', 250000)
.....finding best audio segment.....
('max mins for upsampled video', -1.0, 0.9082138286353888)


  0%|                                                                                           | 0/70 [00:00<?, ?it/s]

('max mins', -1.0, 0.9347432009369123)


C:\Users\tbeleyur\AppData\Local\Continuum\anaconda2\envs\horseshoebat\lib\site-packages\scipy\signal\signaltools.py:491: FutureWarning: Using a non-tuple sequence for multidimensional indexing is deprecated; use `arr[tuple(seq)]` instead of `arr[seq]`. In the future this will be interpreted as an array index, `arr[np.array(seq)]`, which will result either in an error or a different result.
  return x[reverse].conj()
  1%|█▏                                                                                 | 1/70 [00:09<10:45,  9.35s/it]

('max mins', -1.0, 0.9672813302236616)


...

('max mins', -1.0, 0.9770462178004905)


 99%|████████████████████████████████████████████████████████████████████████████████▊ | 69/70 [09:06<00:07,  7.80s/it]

('max mins', -1.0, 0.9335346435590218)


100%|██████████████████████████████████████████████████████████████████████████████████| 70/70 [09:13<00:00,  7.78s/it]


('Best file pairs are: ', 'non_spikey_T0000335.WAV*non_spikey_T0000336.WAV')
Start and end indices around peak:                  start index: 10402598		          end index: 21902598                  total samples:30015488
('AV Sync was above threshold: ', 0.9043721291808902)


### One odd AV sync match : 
There was one annotation, 2018-08-16_2324_144 with 0.59 AV sync cross correlation coefficient. The 45 second long sync audio had a mismatch between the audio and video signals for the first 15 seconds, and then there was relatively good matching. I don't quite understand how this happened - but I'm not using this audio anyway to be sure. 

The matched audio files (sync and annotation) have been deleteed and not uploaded onto OwnCloud. 